In [3]:
import sys
sys.path.insert(0,'../../models/i3D/')

In [5]:
import numpy as np
import pandas as pd
import hashlib
import pickle
import glob
import cv2
from sklearn.model_selection import train_test_split
from soccer_functions import transform_data
from soccer_functions import filter_clips
from soccer_functions import split_video
from soccer_functions import dataframe_from_splits
from soccer_functions import save_clips
from soccer_functions import jupyter_animation
pd.options.mode.chained_assignment = None

pd.set_option('display.max_colwidth', -1)

Using TensorFlow backend.


# Filter CSV - Keep only annotated games for download

In [28]:
file_name = './annotation_isportistics.xlsx'

In [29]:
df = pd.read_excel(file_name, sheet_name='fin_gol_assist_16-17')
df1 = pd.read_excel(file_name, sheet_name='fin_gol_assist_15-16')
df2 = pd.read_excel(file_name, sheet_name='escanteio_15-16')
df3 = pd.read_excel(file_name, sheet_name='escanteio_16-17')
df4 = pd.read_excel(file_name, sheet_name='faltas_15-16')

In [43]:
df

JSON  \
0    europe_uefa-champions-league\2016-2017   
1    europe_uefa-champions-league\2016-2017   
2    europe_uefa-champions-league\2016-2017   
3    europe_uefa-champions-league\2016-2017   
4    europe_uefa-champions-league\2016-2017   
5    europe_uefa-champions-league\2016-2017   
6    europe_uefa-champions-league\2016-2017   
7    europe_uefa-champions-league\2016-2017   
8    europe_uefa-champions-league\2016-2017   
9    europe_uefa-champions-league\2016-2017   
10   europe_uefa-champions-league\2016-2017   
11   europe_uefa-champions-league\2016-2017   
12   europe_uefa-champions-league\2016-2017   
13   europe_uefa-champions-league\2016-2017   
14   europe_uefa-champions-league\2016-2017   
15   europe_uefa-champions-league\2016-2017   
16   europe_uefa-champions-league\2016-2017   
17   europe_uefa-champions-league\2016-2017   
18   europe_uefa-champions-league\2016-2017   
19   europe_uefa-champions-league\2016-2017   
20   europe_uefa-champions-league\2016-2017   
21   europe_uefa-champions-league\2016-2017   
22   europe_uefa-champions-league\2016-2017   
23   europe_uefa-champions-league\2016-2017   
24   europe_uefa-champions-league\2016-2017   
25   europe_uefa-champions-league\2016-2017   
26   europe_uefa-champions-league\2016-2017   
27   europe_uefa-champions-league\2016-2017   
28   europe_uefa-champions-league\2016-2017   
29   europe_uefa-champions-league\2016-2017   
..                                      ...   
329  europe_uefa-champions-league\2016-2017   
330  europe_uefa-champions-league\2016-2017   
331  europe_uefa-champions-league\2016-2017   
332  europe_uefa-champions-league\2016-2017   
333  europe_uefa-champions-league\2016-2017   
334  europe_uefa-champions-league\2016-2017   
335  europe_uefa-champions-league\2016-2017   
336  europe_uefa-champions-league\2016-2017   
337  europe_uefa-champions-league\2016-2017   
338  europe_uefa-champions-league\2016-2017   
339  europe_uefa-champions-league\2016-2017   
340  europe_uefa-champions-league\2016-2017   
341  europe_uefa-champions-league\2016-2017   
342  europe_uefa-champions-league\2016-2017   
343  europe_uefa-champions-league\2016-2017   
344  europe_uefa-champions-league\2016-2017   
345  europe_uefa-champions-league\2016-2017   
346  europe_uefa-champions-league\2016-2017   
347  europe_uefa-champions-league\2016-2017   
348  europe_uefa-champions-league\2016-2017   
349  europe_uefa-champions-league\2016-2017   
350  europe_uefa-champions-league\2016-2017   
351  europe_uefa-champions-league\2016-2017   
352  europe_uefa-champions-league\2016-2017   
353  europe_uefa-champions-league\2016-2017   
354  europe_uefa-champions-league\2016-2017   
355  europe_uefa-champions-league\2016-2017   
356  europe_uefa-champions-league\2016-2017   
357  europe_uefa-champions-league\2016-2017   
358  europe_uefa-champions-league\2016-2017   

                                       Diretorio (jogo)  Video   Fundamento  \
0    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  Assistência   
1    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  Gol           
2    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  FF            
3    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  FF            
4    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  DF            
5    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  Assistência   
6    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  Gol           
7    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  FF            
8    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  DF            
9    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  DF            
10   2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           1.mkv  FF            
11   2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           2.mkv  Gol           
12   2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           2.mkv  Assistência   
13   2016-09-13 - 

In [30]:
all_games = np.unique(np.concatenate((
                np.unique(df['Diretorio (jogo)']),
                np.unique(df1['Diretorio (jogo)']),
                np.unique(df2['Diretorio (jogo)']),
                np.unique(df3['Diretorio (jogo)']),
                np.unique(df4['Diretorio (jogo)'])
                )))

In [37]:
len(all_games)

62

In [6]:
videos = pd.read_csv('SoccerNet_V1.1_Videos_HQ.csv', names=['game', 'link', 'none'])

In [7]:
remove_idx = np.array([index if (row['game']).split('/')[-2] not in all_games else None for index, row in videos.iterrows()])
remove_idx = remove_idx[remove_idx!=None]

In [8]:
filtered_df = videos.drop(remove_idx)
filtered_df.to_csv('SoccerNet_V1.1_Videos_HQ_isportistics.csv', index=False, header=False)

In [38]:
filtered_df

game  \
684  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/video.ini                  
685  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/2_HQ.mkv                   
686  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/1_HQ.mkv                   
687  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/video.ini              
688  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/2_HQ.mkv               
689  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/1_HQ.mkv               
690  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/video.ini            
691  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/2_HQ.mkv             
692  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/1_HQ.mkv             
693  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/video.ini       
694  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/2_HQ.mkv        
695  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/1_HQ.mkv        
696  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/video.ini              
697  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/2_HQ.mkv               
698  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/1_HQ.mkv               
699  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/video.ini           
700  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/2_HQ.mkv            
701  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/1_HQ.mkv            
702  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/video.ini   
703  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/2_HQ.mkv    
704  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/1_HQ.mkv    
705  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/video.ini                  
706  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/2_HQ.mkv                   
707  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/1_HQ.mkv                   
708  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/video.ini         
709  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/2_HQ.mkv          
710  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/1_HQ.mkv          
711  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/video.ini                 
712  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/2_HQ.mkv                  
713  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/1_HQ.mkv                  
..                                                                                            ...                  
846  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/video.ini          
847  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/2_HQ.mkv           
848  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/1_HQ.mkv           
849  /europe_uefa-champions-league/2016-2017/201

# Check if clips are corrected annotated

In [10]:
clip = 5
print(clip)
df.loc[clip]

5


JSON                europe_uefa-champions-league\2016-2017   
Diretorio (jogo)    2016-09-13 - 21-45 Barcelona 7 - 0 Celtic
Video               1.mkv                                    
Fundamento          Assistência                              
Tempo (video)       00:35:37                                 
Como                pe esquerdo                              
Ass.                s                                        
Reb.                NaN                                      
Pen.                NaN                                      
Falta               NaN                                      
Obs.:               NaN                                      
Obs. Ass.           passe rasteiro                           
Desvio              NaN                                      
Escanteio           NaN                                      
Fin. Rast.          NaN                                      
Espalmada           NaN                                      
Name: 5,

In [36]:
filtered_df

game  \
684  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/video.ini                  
685  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/2_HQ.mkv                   
686  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Malmo FF 0 - 5 Paris SG/1_HQ.mkv                   
687  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/video.ini              
688  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/2_HQ.mkv               
689  /europe_uefa-champions-league/2015-2016/2016-04-05 - 21-45 Bayern Munich 1 - 0 Benfica/1_HQ.mkv               
690  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/video.ini            
691  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/2_HQ.mkv             
692  /europe_uefa-champions-league/2015-2016/2015-12-09 - 22-45 D. Zagreb 0 - 2 Bayern Munich/1_HQ.mkv             
693  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/video.ini       
694  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/2_HQ.mkv        
695  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 Shakhtar Donetsk 3 - 4 Real Madrid/1_HQ.mkv        
696  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/video.ini              
697  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/2_HQ.mkv               
698  /europe_uefa-champions-league/2015-2016/2015-11-25 - 20-00 CSKA Moscow 0 - 2 Wolfsburg/1_HQ.mkv               
699  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/video.ini           
700  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/2_HQ.mkv            
701  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Maccabi Tel Aviv 0 - 4 Chelsea/1_HQ.mkv            
702  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/video.ini   
703  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/2_HQ.mkv    
704  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Bayern Munich 4 - 0 Olympiakos Piraeus/1_HQ.mkv    
705  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/video.ini                  
706  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/2_HQ.mkv                   
707  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 Barcelona 6 - 1 AS Roma/1_HQ.mkv                   
708  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/video.ini         
709  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/2_HQ.mkv          
710  /europe_uefa-champions-league/2015-2016/2015-11-25 - 22-45 B. Monchengladbach 4 - 2 Sevilla/1_HQ.mkv          
711  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/video.ini                 
712  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/2_HQ.mkv                  
713  /europe_uefa-champions-league/2015-2016/2015-11-24 - 22-45 FC Porto 0 - 2 Dyn. Kiev/1_HQ.mkv                  
..                                                                                            ...                  
846  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/video.ini          
847  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/2_HQ.mkv           
848  /europe_uefa-champions-league/2016-2017/2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona/1_HQ.mkv           
849  /europe_uefa-champions-league/2016-2017/201

In [9]:
df[df['Fundamento'] == 'TF']

JSON  \
20   europe_uefa-champions-league\2016-2017   
34   europe_uefa-champions-league\2016-2017   
100  europe_uefa-champions-league\2016-2017   
106  europe_uefa-champions-league\2016-2017   
110  europe_uefa-champions-league\2016-2017   
114  europe_uefa-champions-league\2016-2017   
122  europe_uefa-champions-league\2016-2017   
145  europe_uefa-champions-league\2016-2017   
154  europe_uefa-champions-league\2016-2017   
258  europe_uefa-champions-league\2016-2017   
261  europe_uefa-champions-league\2016-2017   
283  europe_uefa-champions-league\2016-2017   

                                       Diretorio (jogo)  Video Fundamento  \
20   2016-09-13 - 21-45 Barcelona 7 - 0 Celtic           2.mkv  TF          
34   2016-09-13 - 21-45 Dyn. Kiev 1 - 2 Napoli           2.mkv  TF          
100  2016-10-19 - 21-45 Paris SG 3 - 0 Basel             1.mkv  TF          
106  2016-10-19 - 21-45 Paris SG 3 - 0 Basel             1.mkv  TF          
110  2016-10-19 - 21-45 Paris SG 3 - 0 Basel             2.mkv  TF          
114  2016-10-19 - 21-45 Paris SG 3 - 0 Basel             2.mkv  TF          
122  2016-11-01 - 20-45 Besiktas 1 - 1 Napoli            1.mkv  TF          
145  2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona  2.mkv  TF          
154  2016-11-23 - 22-45 Arsenal 2 - 2 Paris SG           2.mkv  TF          
258  2017-03-07 - 22-45 Napoli 1 - 3 Real Madrid         1.mkv  TF          
261  2017-03-07 - 22-45 Napoli 1 - 3 Real Madrid         1.mkv  TF          
283  2017-03-08 - 22-45 Barcelona 6 - 1 Paris SG         2.mkv  TF          

    Tempo (video)         Como Ass. Reb. Pen. Falta Obs.: Obs. Ass. Desvio  \
20   00:44:01      pe esquerdo  NaN  NaN  NaN  NaN   fora  NaN       NaN     
34   00:19:47      pe direito   NaN  NaN  NaN  NaN   NaN   NaN       NaN     
100  00:11:38      cabeça       NaN  NaN  NaN  NaN   NaN   NaN       NaN     
106  00:42:19      cabeça       NaN  NaN  NaN  NaN   NaN   NaN       NaN     
110  00:08:30      cabeça       NaN  NaN  NaN  NaN   fora  NaN       NaN     
114  00:26:59      cabeça       NaN  NaN  NaN  NaN   NaN   NaN       NaN     
122  00:39:54      pe esquerdo  NaN  NaN  NaN  NaN   fora  NaN       NaN     
145  00:20:48      pe esquerdo  NaN  NaN  NaN  NaN   NaN   NaN       NaN     
154  00:16:07      pe direito   NaN  NaN  NaN  s     fora  NaN       NaN     
258  00:34:59      pe direito   NaN  NaN  NaN  NaN   NaN   NaN       NaN     
261  00:43:14      pe direito   NaN  NaN  NaN  NaN   NaN   NaN       NaN     
283  00:20:39      pe esquerdo  NaN  NaN  NaN  NaN   fora  NaN       NaN     

    Escanteio Fin. Rast. Espalmada  
20   NaN       s          NaN       
34   NaN       NaN        NaN       
100  NaN       NaN        NaN       
106  NaN       NaN        NaN       
110  NaN       NaN        NaN       
114  NaN       NaN        NaN       
122  NaN       NaN        NaN       
145  NaN       NaN        NaN       
154  NaN       NaN        NaN       
258  NaN       s          NaN       
261  NaN       s          NaN       
283  NaN       NaN        NaN

In [11]:
videos_path = glob.glob('./*/*/*/' + df.loc[clip]['Diretorio (jogo)'] + '/' +  df.loc[clip]['Video'].split('.')[0] + '_HQ.mkv')[0]

In [12]:
cap = cv2.VideoCapture(videos_path)
fps = cap.get(cv2.CAP_PROP_FPS)
height = 224
width = 224
video_length = 24
video = np.zeros(shape=(video_length, height, width, 3), dtype=np.uint8)

In [23]:
np.unique(df['Diretorio (jogo)'], return_counts=True)[0]

array(['2016-09-13 - 21-45 Barcelona 7 - 0 Celtic',
       '2016-09-13 - 21-45 Dyn. Kiev 1 - 2 Napoli',
       '2016-09-28 - 21-45 Ludogorets 1 - 3 Paris SG',
       '2016-09-28 - 21-45 Napoli 4 - 2 Benfica',
       '2016-10-19 - 21-45 Barcelona 4 - 0 Manchester City',
       '2016-10-19 - 21-45 Paris SG 3 - 0 Basel',
       '2016-11-01 - 20-45 Besiktas 1 - 1 Napoli',
       '2016-11-01 - 22-45 Manchester City 3 - 1 Barcelona',
       '2016-11-23 - 22-45 Arsenal 2 - 2 Paris SG',
       '2016-11-23 - 22-45 Celtic 0 - 2 Barcelona',
       '2016-11-23 - 22-45 Napoli 0 - 0 Dyn. Kiev',
       '2016-12-06 - 22-45 Benfica 1 - 2 Napoli',
       '2017-02-14 - 22-45 Paris SG 4 - 0 Barcelona',
       '2017-02-15 - 22-45 Real Madrid 3 - 1 Napoli',
       '2017-03-07 - 22-45 Napoli 1 - 3 Real Madrid',
       '2017-03-08 - 22-45 Barcelona 6 - 1 Paris SG',
       '2017-04-12 - 21-45 Bayern Munich 1 - 2 Real Madrid',
       '2017-04-18 - 21-45 Real Madrid 4 - 2 Bayern Munich',
       '2017-05-02 - 21-

In [13]:
t = df.loc[clip]['Tempo (video)']
seconds = (t.hour * 60 + t.minute) * 60 + t.second
start_frame = seconds*fps - 1
end_frame = (seconds+4)*fps

In [14]:
cap.set(cv2.CAP_PROP_POS_FRAMES, start_frame-1)
actual = int(start_frame)
frame_list = np.linspace(start_frame, end_frame, 24, dtype=int)
pos = 0
while pos != video_length:
    if actual in frame_list:
        _ , frame = cap.read()
        video[pos] = cv2.resize(frame, (height, width))
        pos +=1
    else:
        _ , frame = cap.read()
    actual += 1

In [1]:
!pwd

/home/ubuntu/ai-stats-soccer/data/SoccerNet


In [11]:
video = np.load('../../models/i3D/clips/2_HQ.mkv_39493.npy')

In [12]:
%%capture
%matplotlib inline
ani = jupyter_animation(video)

In [14]:
ani